## Imports

In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import subprocess
import plotly.express as px
import pandas as pd
import os
import subprocess
import itertools
# plotting libraries
from plotly.subplots import make_subplots
import plotly.graph_objects as go

## Utility Functions

In [ ]:
def plot_simulation_results(df, fig_height=500, fig_width=800):
    # Calculate Acceleration and Jerk
    df['Acceleration'] = df['EgoSpeed'].diff() / df['Time'].diff()
    df['Jerk'] = df['Acceleration'].diff() / df['Time'].diff()

    # Plot Acceleration and Jerk on the same plot
    fig_acc_jerk = go.Figure()
    fig_acc_jerk.add_trace(go.Scatter(x=df['Time'], y=df['Acceleration'], mode='lines', name='Acceleration'))
    fig_acc_jerk.add_trace(go.Scatter(x=df['Time'], y=df['Jerk'], mode='lines', name='Jerk'))
    
    fig_acc_jerk.update_layout(height=fig_height, width=fig_width, title='Acceleration and Jerk', xaxis_title='Time', yaxis_title='Values')
    fig_acc_jerk.show()
    
    fig1 = go.Figure()
    fig1.add_trace(go.Scatter(x=df['Time'], y=df['Torque'], mode='lines', name='Torque'))
    fig1.update_layout(height=fig_height, width=fig_width, title='Torque', xaxis_title='Time', yaxis_title='Values')
    fig1.show()

    fig2 = go.Figure()
    fig2.add_trace(go.Scatter(x=df['Time'], y=df['Error'], mode='lines', name='Error'))
    fig2.update_layout(height=fig_height, width=fig_width, title='Error', xaxis_title='Time', yaxis_title='Error')
    fig2.show()

    fig3 = go.Figure()
    fig3.add_trace(go.Scatter(x=df['Time'], y=df['EgoSpeed'], mode='lines', name='EgoSpeed'))
    fig3.add_trace(go.Scatter(x=df['Time'], y=df['ACCTargetSpeed'], mode='lines', name='ACCTargetSpeed'))
    fig3.add_trace(go.Scatter(x=df['Time'], y=df['LeadSpeed'], mode='lines', name='LeadSpeed'))
    fig3.add_trace(go.Scatter(x=df['Time'], y=df['DriverSetSpeed'], mode='lines', name='DriverSetSpeed'))
    fig3.update_layout(height=fig_height, width=fig_width, title='Speeds', xaxis_title='Time (s)', yaxis_title='Speed')
    fig3.show()

    fig = make_subplots(rows=1, cols=2, subplot_titles=('Distance Lead', 'Time Gaps'))
    fig.add_trace(go.Scatter(x=df['Time'], y=df['Gap(m)'], mode='lines', name='Distance to Lead'), row=1, col=1)
    fig.add_trace(go.Scatter(x=df['Time'], y=df['SafeDistance'], mode='lines', name='SafeDistance'), row=1, col=1)
    fig.add_trace(go.Scatter(x=df['Time'], y=df['TrueTimeGap'], mode='lines', name='TrueTimeGap'), row=1, col=2)
    fig.add_trace(go.Scatter(x=df['Time'], y=df['TargetTimeGap'], mode='lines', name='TargetTimeGap'), row=1, col=2)
    fig.update_layout(height=fig_height, width=fig_width * 1.5, title_text="Torque and Time Gaps / Distance")
    fig.show()

## Compile Cpp Code (Before running tests)

In [19]:
# Get all .cpp and .hpp files from the src folder
cpp_files = [os.path.join('src/', f) for f in os.listdir('src') if f.endswith('.cpp')]
hpp_files = [os.path.join('src/', f) for f in os.listdir('src') if f.endswith('.hpp')]

# Compile the files
compile_command = ['g++', '-o', 'ACCTest'] + cpp_files + hpp_files
result = subprocess.run(compile_command, capture_output=True, text=True)
if result.returncode != 0:
    print("Compilation failed with the following errors:")
    print(result.stderr)
else:
    print("Compilation succeeded.")

Compilation succeeded.


## Only Cruise Control Tests

In [21]:
# Subprocess to run the simulation
result = subprocess.run(['./ACCTest.exe', '1'], capture_output=True, text=True)
print(result.stdout)

#  Read the CSV file
df = pd.read_csv('simulation_log.csv')

# Calculate Jerk (rate of change of acceleration)
df['Acceleration'] = df['Actual Speed'].diff() / df['Time'].diff()
df['Jerk'] = df['Acceleration'].diff() / df['Time'].diff()


# Calculate the RMSE (Root Mean Square Error)
rmse = ((df['Error'] ** 2).mean()) ** 0.5
print(f'Average RMSE Error: {rmse}')
# Interactive plot for Error, Actual Speed, and Target Speed
fig = px.line(df, x='Time', y=['Error', 'Actual Speed', 'Target Speed'], title='Speeds')
fig.update_layout(xaxis_title='Time', yaxis_title='Values')
fig.show()

# Interactive plot for Error, Actual Speed, and Target Speed
fig = px.line(df, x='Time', y=['Acceleration', 'Jerk'], title='Acceleration and Jerk')
fig.update_layout(xaxis_title='Time', yaxis_title='Values')
fig.show()

# Interactive plot for Torque
fig = px.line(df, x='Time', y='Torque', title='Torque over Time')
fig.update_layout(xaxis_title='Time', yaxis_title='Torque')
fig.show()

Running simulation with one vehicle...
Loaded ACC Controller Parameters: 
Time Gap: 2
Time Gap Tolerance: 1
Kp: 120
Ki: 3
Kd: 0
d_Kp: 0.4
d_Ki: 0
d_Kd: 0
PID Speed Control: 1
Overshoot: 0.00798783%
Simulation completed!

Average RMSE Error: 0.8318899037759904


## Adaptive Cruise Control Test

In [22]:
# Run the Compiled File
gains_df = pd.read_csv('gains.csv')
gains_df.loc[gains_df['parameter'] == 'pid_speed_control', 'value'] = 1
gains_df.to_csv('gains.csv', index=False)

# Run the Compiled File
result = subprocess.run(['./ACCTest.exe', '2'], capture_output=True, text=True)
print('\n'.join(result.stdout.splitlines()[:11]))
print('\n'.join(result.stdout.splitlines()[-3:-1]))

Running simulation with two vehicles...
Loaded ACC Controller Parameters: 
Time Gap: 2
Time Gap Tolerance: 1
Kp: 120
Ki: 3
Kd: 0
d_Kp: 0.4
d_Ki: 0
d_Kd: 0
PID Speed Control: 1
Stop Time: 3.66293
Overshoot: -0.484595%


### Parameter Tuning and Visualization

In [23]:
gains_df = pd.read_csv('gains.csv')
gains_df.loc[gains_df['parameter'] == 'pid_speed_control', 'value'] = 1
gains_df.to_csv('gains.csv', index=False)

# Run the Compiled File
result = subprocess.run(['./ACCTest.exe', '2'], capture_output=True, text=True)
# Load the results into a DataFrame
df = pd.read_csv('simulation_log_ACC.csv')
# df = pd.read_csv('oldLogs/brake_check/simulation_log_ACC_brake_check.csv')

plot_simulation_results(df)

In [24]:
gains_df = pd.read_csv('gains.csv')
gains_df.loc[gains_df['parameter'] == 'pid_speed_control', 'value'] = 1
gains_df.to_csv('gains.csv', index=False)

# Run the Compiled File
result = subprocess.run(['./ACCTest.exe', '3'], capture_output=True, text=True)
# Load the results into a DataFrame
df = pd.read_csv('simulation_log_ACC.csv')
# df = pd.read_csv('oldLogs/brake_check/simulation_log_ACC_brake_check.csv')

plot_simulation_results(df)

## Hyperparameter Search

In [ ]:
def update_gains_csv(file_path, time_gap=15, Kp=15, Kd=15, Ki=15):
    # Read the CSV file
    gains_df = pd.read_csv(file_path)
    
    # Make the necessary edits
    gains_df.loc[gains_df['parameter'] == 'time_gap', 'value'] = time_gap
    gains_df.loc[gains_df['parameter'] == 'Kp', 'value'] = Kp
    gains_df.loc[gains_df['parameter'] == 'Kd', 'value'] = Kd
    gains_df.loc[gains_df['parameter'] == 'Ki', 'value'] = Ki
    
    # Save the changes back to the CSV file
    gains_df.to_csv(file_path, index=False)

# Usage
update_gains_csv('gains.csv', time_gap=10, Kp=20, Kd=20, Ki=20)


In [ ]:
time_gap_range = np.linspace(1, 25, 5)
Kp_range = np.linspace(1, 200, 5)
Kd_range = np.linspace(1, 200, 5)
Ki_range = np.linspace(1, 200, 5)

results = []
for time_gap in time_gap_range:
    for Kp in Kp_range:
        for Kd in Kd_range:
            for Ki in Ki_range:
                update_gains_csv('gains.csv', time_gap=time_gap, Kp=Kp, Kd=Kd, Ki=Ki)

                # Run the executable
                result = subprocess.run(['./ACCTest.exe'], capture_output=True, text=True)

                # Print the output
                # print(result.stdout)
                # print(result.stderr)

                df = pd.read_csv('simulation_log_ACC.csv')
                df['Time'] = df['Time'] / 10
                # Get the max and min values for each column except 'Time'
                max_torq = df["Torque"].max()
                min_distance = df['Gap(m)'].min()

                # Store the results
                results.append({
                    'time_gap': time_gap,
                    'Kp': Kp,
                    'Kd': Kd,
                    'Ki': Ki,
                    'max_torque': max_torq,
                    'min_distance': min_distance
                })

# # Run the executable
# result = subprocess.run(['./VehiclePIDController.exe'], capture_output=True, text=True)

NameError: name 'np' is not defined

In [ ]:
results_df = pd.DataFrame(results)
results_df.to_excel('results.xlsx', index=False)

In [ ]:
# Remove rows where min_distance is negative
filtered_df = results_df[results_df['min_distance'] >= 0]

# Get min and max ranges for Kp, Ki, Kd, and time_gap
min_max_ranges = {
    'Kp': (filtered_df['Kp'].min(), filtered_df['Kp'].max()),
    'Ki': (filtered_df['Ki'].min(), filtered_df['Ki'].max()),
    'Kd': (filtered_df['Kd'].min(), filtered_df['Kd'].max()),
    'time_gap': (filtered_df['time_gap'].min(), filtered_df['time_gap'].max())
}

# Get modes for Kp, Ki, Kd, and time_gap
modes = {
    'Kp': filtered_df['Kp'].mode()[0],
    'Ki': filtered_df['Ki'].mode()[0],
    'Kd': filtered_df['Kd'].mode()[0],
    'time_gap': filtered_df['time_gap'].mode()[0]
}

print(min_max_ranges)
print(modes)

{'Kp': (50.75, 200.0), 'Ki': (1.0, 50.75), 'Kd': (1.0, 200.0), 'time_gap': (7.0, 25.0)}
{'Kp': 200.0, 'Ki': 1.0, 'Kd': 200.0, 'time_gap': 25.0}


In [ ]:
filtered_df.to_excel('filtered_results.xlsx', index=False)

In [ ]:
# Time Gap	Kp	Kd	Ki
# Time_Gap		Time used to calculate the safe vehicle following distance	s	1.0 /2.5	.1	5
# Kp				50.75	250.0
# Kd					0	50.75
# KI					0	200.0
# Create a table for all combinations of the values
time_gap_range = np.linspace(1, 5, 5)
Kp_range = np.linspace(50.75, 250, 5)
Kd_range = np.linspace(0, 50.75, 5)

combinations = list(itertools.product(time_gap_range, Kp_range, Kd_range, Ki_range))

# Convert the combinations to a DataFrame
combinations_df = pd.DataFrame(combinations, columns=['time_gap', 'Kp', 'Kd', 'Ki'])

# Display the DataFrame
combinations_df

time_gap      Kp     Kd      Ki
0         1.0   50.75   0.00    1.00
1         1.0   50.75   0.00   50.75
2         1.0   50.75   0.00  100.50
3         1.0   50.75   0.00  150.25
4         1.0   50.75   0.00  200.00
..        ...     ...    ...     ...
620       5.0  250.00  50.75    1.00
621       5.0  250.00  50.75   50.75
622       5.0  250.00  50.75  100.50
623       5.0  250.00  50.75  150.25
624       5.0  250.00  50.75  200.00

[625 rows x 4 columns]